In [2]:
import pandas as pd
import os

In [3]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "new_constructions/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [47]:
data_frames = []

# base cols RegionID,SizeRank,RegionName,RegionType,StateName

exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    # "Value Type",
    "Home Type",
]

price_data_frames = []
price_per_sqft_data_frames = []
count_data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        if "sfrcondo" in filename:
            cur_df["Home Type"] = "all homes"
        elif "sfr" in filename:
            cur_df["Home Type"] = "SFR"
        elif "condo" in filename:
            cur_df["Home Type"] = "condo/co-op only"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        if "sale_price_per_sqft" in filename:
            # cur_df["Value Type"] = "Sale Price Per Sqft"
            # Perform pivot
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name="Sale Price per Sqft",
            )
            price_per_sqft_data_frames.append(cur_df)

        elif "sale_price_uc" in filename:
            # cur_df["Value Type"] = "Sale Price"
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name="Sale Price",
            )
            price_data_frames.append(cur_df)

        elif "count" in filename:
            # cur_df["Value Type"] = "Count"
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name="Count",
            )
            count_data_frames.append(cur_df)


combined_price = pd.concat(price_data_frames)
combined_price_per = pd.concat(price_per_sqft_data_frames)
combined_count = pd.concat(count_data_frames)

matching_cols = [
    "RegionID",
    "Date",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    # "Value Type",
    "Home Type",
]

combined_df = pd.merge(
    combined_price,
    combined_price_per,
    on=matching_cols,
    how="outer",
)
combined_df = pd.merge(
    combined_df,
    combined_count,
    on=matching_cols,
    how="outer",
)

combined_df

processing Metro_new_con_sales_count_raw_uc_condo_month.csv
processing Metro_new_con_median_sale_price_per_sqft_uc_sfr_month.csv
processing Metro_new_con_sales_count_raw_uc_sfr_month.csv
processing Metro_new_con_median_sale_price_uc_sfrcondo_month.csv
processing Metro_new_con_median_sale_price_per_sqft_uc_condo_month.csv
processing Metro_new_con_sales_count_raw_uc_sfrcondo_month.csv
processing Metro_new_con_median_sale_price_uc_condo_month.csv
processing Metro_new_con_median_sale_price_uc_sfr_month.csv
processing Metro_new_con_median_sale_price_per_sqft_uc_sfrcondo_month.csv


RegionID  SizeRank     RegionName RegionType StateName  \
0        102001         0  United States    country       NaN   
1        102001         0  United States    country       NaN   
2        102001         0  United States    country       NaN   
3        102001         0  United States    country       NaN   
4        102001         0  United States    country       NaN   
...         ...       ...            ...        ...       ...   
49482    845162       535   Granbury, TX        msa        TX   
49483    845162       535   Granbury, TX        msa        TX   
49484    845162       535   Granbury, TX        msa        TX   
49485    845162       535   Granbury, TX        msa        TX   
49486    845162       535   Granbury, TX        msa        TX   

              Home Type        Date  Sale Price  Sale Price per Sqft    Count  
0                   SFR  2018-01-31    309000.0           137.412316  33940.0  
1             all homes  2018-01-31    314596.0           140.504620  37135.0  
2      condo/co-op only  2018-01-31    388250.0           238.300000   3195.0  
3                   SFR  2018-02-28    309072.5           137.199170  33304.0  
4             all homes  2018-02-28    314608.0           140.304966  36493.0  
...                 ...         ...         ...                  ...      ...  
49482         all homes  2023-09-30         NaN                  NaN     26.0  
49483               SFR  2023-10-31         NaN                  NaN     24.0  
49484         all homes  2023-10-31         NaN                  NaN     24.0  
49485               SFR  2023-11-30         NaN                  NaN     16.0  
49486         all homes  2023-11-30         NaN                  NaN     16.0  

[49487 rows x 10 columns]

In [48]:
final_df = combined_df
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df

Region ID  Size Rank         Region Region Type State  \
0         102001          0  United States     country   NaN   
1         102001          0  United States     country   NaN   
2         102001          0  United States     country   NaN   
3         102001          0  United States     country   NaN   
4         102001          0  United States     country   NaN   
...          ...        ...            ...         ...   ...   
49482     845162        535   Granbury, TX         msa    TX   
49483     845162        535   Granbury, TX         msa    TX   
49484     845162        535   Granbury, TX         msa    TX   
49485     845162        535   Granbury, TX         msa    TX   
49486     845162        535   Granbury, TX         msa    TX   

              Home Type        Date  Sale Price  Sale Price per Sqft    Count  
0                   SFR  2018-01-31    309000.0           137.412316  33940.0  
1             all homes  2018-01-31    314596.0           140.504620  37135.0  
2      condo/co-op only  2018-01-31    388250.0           238.300000   3195.0  
3                   SFR  2018-02-28    309072.5           137.199170  33304.0  
4             all homes  2018-02-28    314608.0           140.304966  36493.0  
...                 ...         ...         ...                  ...      ...  
49482         all homes  2023-09-30         NaN                  NaN     26.0  
49483               SFR  2023-10-31         NaN                  NaN     24.0  
49484         all homes  2023-10-31         NaN                  NaN     24.0  
49485               SFR  2023-11-30         NaN                  NaN     16.0  
49486         all homes  2023-11-30         NaN                  NaN     16.0  

[49487 rows x 10 columns]

In [49]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)